In [ ]:
## The code below will allow optimization of hyperparameter
%pylab inline
from Chempy.parameter import ModelParameters
a = ModelParameters()

In [ ]:
# To plot neural network error against learning rate for optimization

from Chempy.neural import create_network,calculate_errors

# Now create and train the neural network for optimal hyperparameters
learning_rate = 0.003
epoch, loss = create_network(learning_rate=learning_rate)
error,std,max_err = calculate_errors('test')

In [ ]:
mean_err = np.mean(error)
std_err = np.std(error)
mean_max_err = np.mean(max_err)
print('Mean error is %.5f +/- %.5f with mean maximum %.5f' %(mean_err,std_err,mean_max_err))

In [ ]:
max_err

In [ ]:
np.max(max_err)

In [ ]:
dat=plt.hist(max_err,bins=100)

In [ ]:
from Chempy.neural import max_err_corner_plot
max_err_corner_plot('test')

In [ ]:
plt.plot(epoch,loss)

In [ ]:
sol_dat = np.load('Chempy/input/stars/Proto-sun.npy')
sol_dat = array([ ( 0.  ,  4.56),
       ( 0.06,  0.01)], 
      dtype=[('He', '<f8'),  ('age', '<f8')])

In [ ]:
sol_dat

In [ ]:
np.save('Chempy/input/stars/Proto-sun.npy',sol_dat)

In [ ]:
sol_dat.dtype.names

In [ ]:
from Chempy.wrapper import multi_star_optimization
multi_star_optimization()

In [ ]:
from Chempy.plot_mcmc import restructure_chain
restructure_chain('karakas10_neural/')


In [ ]:
%pylab inline
from Chempy.parameter import ModelParameters
a = ModelParameters()

In [ ]:
from Chempy.neural import neural_output
from Chempy.cem_function import cem_real2,posterior_function_returning_predictions,extract_parameters_and_priors
param = [-2.8,-3.06,-0.83,-0.26,0.43,0.36]
a = extract_parameters_and_priors(param,a)
a.UseNeural = False
abun,_ = cem_real2(a)

In [ ]:
a = ModelParameters()
a.UseNeural = True
param = [-2.8,-3.06,-0.83,-0.26,0.43,0.36]
a = extract_parameters_and_priors(param,a)
abun2,_ = cem_real2(a)

In [ ]:
print(abun)
print(abun2)

In [ ]:
err = []
ab1 = []
ab2 = []
for i,item in enumerate(abun2):
    if item !=0:
        err.append(abun[i]-item)
        ab1.append(abun[i])
        ab2.append(item)
#plt.plot(range(len(err)),err)
plt.plot(range(len(ab1)),ab1,label='Chempy')
plt.plot(range(len(ab1)),ab2,label='Neural')
plt.legend()

In [ ]:
neural_output(param)

In [ ]:
a.UseNeural=False
posterior_function_returning_predictions((param,a))

In [ ]:
from Chempy.wrapper import multi_star_optimization
multi_star_optimization()
from Chempy.plot_mcmc import plot_mcmc_chain_with_prior,restructure_chain
restructure_chain('mcmc/')


In [ ]:
%pylab inline

In [ ]:
from Chempy.parameter import ModelParameters
a = ModelParameters()

N = a.training_size # No. data points per parameter
widths = a.training_widths # Gaussian widths for parameters	
widths = [3.,3.,3.,3.,3.,3.]

# Create 1d grid of data points equally spaced in probability space 
prob = np.linspace(1/(N+1), 1-1/(N+1), N)

In [ ]:
gaussian.ppf(prob)

In [ ]:
from scipy.stats import norm as gaussian

In [ ]:
prob = np.linspace(1/(N+1), 1-1/(N+1), N)
grids = [gaussian.ppf(prob) for _ in range(len(a.p0))] # Normalize to unit Gaussian
norm_grid = np.array(np.meshgrid(*grids)).T.reshape(-1,len(a.p0))

# Create grid in parameter space
param_grid = [item*widths+a.p0 for item in norm_grid]


In [ ]:
%pylab inline
from Chempy.parameter import ModelParameters
from Chempy.cem_function import posterior_function_returning_predictions
a = ModelParameters()
import warnings
warnings.filterwarnings("ignore")

In [ ]:
lower = np.zeros(len(a.p0))
upper = np.zeros(len(a.p0))
names = ['verif','test'] # Two datasets

a.verif_test_sizes = [5,5]

# Set upper/lower bounds in parameter space
for i,param_name in enumerate(a.to_optimize):
    lower[i], upper[i] = a.constraints.get(param_name)
    
for j ,name in enumerate(names): # Create both test sets
    param_grid = []
    model_abundances = []
    for k in range(a.verif_test_sizes[j]): 
        param = np.ones(len(a.p0))*np.inf # To ensure initial value is not in range
        for i in range(len(a.p0)):
            param[i] = np.inf
            while param[i] > upper[i] or param[i] < lower[i]: # Continue until param is in correct range
                param[i] = np.random.normal(loc=a.p0[i],scale=a.test_widths[i])
        param_grid.append(param)
        abundances,_ = posterior_function_returning_predictions((param,a))
        model_abundances.append(abundances)
        if k%100==0 :
            print("Calculating %s abundance set %d of %d" %(name,k,a.verif_test_sizes[j]))
    np.save("Neural/"+name+"_param_grid.npy",param_grid)
    np.save("Neural/"+name+"_abundances.npy",model_abundances)

In [ ]:
lower

In [ ]:
	for i,name in enumerate(names): # Create two identically distributed datasets
		length = a.verif_test_sizes[i]
		param_grid = []
		
		# Distribute data with prior widths
		for _ in range(length):
			param_grid.append(np.random.normal(size = len(a.p0), loc = a.p0,
									scale = a.test_widths))
			np.save("Neural/"+name+"_param_grid.npy",param_grid)
    
		model_abundances = []
		for j,jtem in enumerate(param_grid):
			abundances,_ = posterior_function_returning_predictions((jtem,a))
			model_abundances.append(abundances)
			if j%100 == 0:
				#print("Calculating %s abundance set %d of %d" %(name,j,length))
				continue
 		
 		# Save abundance table
		np.save("Neural/"+name+"_abundances.npy",model_abundances)


In [ ]:
param_grid

In [ ]:
lower

In [ ]:
upper

In [3]:
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [ ]:
from Chempy.neural import verification_and_testing
%timeit -r 1 -n 1 verification_and_testing()

gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
Calculating verif abundance set 0 of 10000
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir is empty
gas reservoir 

too few gas requested infall needed=  0.0 gas there =  0.00585464290008 total SFR =  [  7.24969442e-05   7.24969442e-03   1.36096009e-02   1.91616251e-02
   2.39809712e-02   2.81366555e-02   3.16919828e-02   3.47049876e-02
   3.72288424e-02   3.93122360e-02   4.09997236e-02   4.23320506e-02
   4.33464524e-02   4.40769320e-02   4.45545163e-02   4.48074933e-02
   4.48616315e-02   4.47403827e-02   4.44650690e-02] gas needed =  0.00152439353652 corona =  0.778756245964 sfe =  29.227699537 dt =  0.5
too few gas requested infall needed=  0.0 gas there =  0.00604365432976 total SFR =  [  7.24969442e-05   7.24969442e-03   1.36096009e-02   1.91616251e-02
   2.39809712e-02   2.81366555e-02   3.16919828e-02   3.47049876e-02
   3.72288424e-02   3.93122360e-02   4.09997236e-02   4.23320506e-02
   4.33464524e-02   4.40769320e-02   4.45545163e-02   4.48074933e-02
   4.48616315e-02   4.47403827e-02   4.44650690e-02] gas needed =  0.00153304892192 corona =  0.79245336859 sfe =  29.227699537 dt =  0.5
t

too few gas requested infall needed=  0.00134054571931 gas there =  0.00798484620884 total SFR =  [  8.90758316e-05   6.10671588e-02   9.20065756e-02   1.03965987e-01
   1.04426609e-01   9.83336921e-02   8.88924239e-02   7.81254794e-02
   6.72613840e-02   5.70032318e-02   4.77131540e-02   3.95377515e-02
   3.24923921e-02   2.65170342e-02   2.15124953e-02   1.73634159e-02
   1.39522757e-02   1.11674790e-02   8.90758316e-03] gas needed =  0.00932539191474 corona =  1.64393095366 sfe =  3.48429239235 dt =  0.5
too few gas requested infall needed=  0.00102370854368 gas there =  0.0065867417971 total SFR =  [  8.90758316e-05   6.10671588e-02   9.20065756e-02   1.03965987e-01
   1.04426609e-01   9.83336921e-02   8.88924239e-02   7.81254794e-02
   6.72613840e-02   5.70032318e-02   4.77131540e-02   3.95377515e-02
   3.24923921e-02   2.65170342e-02   2.15124953e-02   1.73634159e-02
   1.39522757e-02   1.11674790e-02   8.90758316e-03] gas needed =  0.00761045033054 corona =  1.6650183333 sfe =  

too few gas requested infall needed=  0.0 gas there =  0.0208356521305 total SFR =  [ 0.00024529  0.02747703  0.04605335  0.05789139  0.06468657  0.06776191
  0.06814411  0.0666249   0.06381018  0.06015946  0.05601739  0.0516389
  0.04720924  0.04285984  0.03868091  0.03473133  0.03104642  0.02764407
  0.0245294 ] gas needed =  0.00395565593985 corona =  1.19196253184 sfe =  11.9346172771 dt =  0.5
too few gas requested infall needed=  0.0 gas there =  0.0192865475606 total SFR =  [ 0.00024529  0.02747703  0.04605335  0.05789139  0.06468657  0.06776191
  0.06814411  0.0666249   0.06381018  0.06015946  0.05601739  0.0516389
  0.04720924  0.04285984  0.03868091  0.03473133  0.03104642  0.02764407
  0.0245294 ] gas needed =  0.00359122046478 corona =  1.21262450356 sfe =  11.9346172771 dt =  0.5
too few gas requested infall needed=  0.0 gas there =  0.0177624322888 total SFR =  [ 0.00024529  0.02747703  0.04605335  0.05789139  0.06468657  0.06776191
  0.06814411  0.0666249   0.06381018  0

too few gas requested infall needed=  0.00936065558687 gas there =  0.00132387967624 total SFR =  [ 0.00018808  0.0188083   0.03273777  0.04273758  0.04959274  0.05395077
  0.05634409  0.05720904  0.05690182  0.05571193  0.0538735   0.05157478
  0.04896609  0.04616651  0.04326943  0.04034725  0.0374552   0.03463463
  0.03191565] gas needed =  0.0106845351695 corona =  1.05407966766 sfe =  3.241566581 dt =  0.5
too few gas requested infall needed=  0.00860046504143 gas there =  0.00124528306566 total SFR =  [ 0.00018808  0.0188083   0.03273777  0.04273758  0.04959274  0.05395077
  0.05634409  0.05720904  0.05690182  0.05571193  0.0538735   0.05157478
  0.04896609  0.04616651  0.04326943  0.04034725  0.0374552   0.03463463
  0.03191565] gas needed =  0.00984574802109 corona =  1.06354817952 sfe =  3.241566581 dt =  0.5
too few gas requested infall needed=  0.062543086089 gas there =  2.72757060556e-06 total SFR =  [  3.22619903e-05   9.53469954e-02   1.31822831e-01   1.36689614e-01
   1.

...

too few gas requested infall needed=  0.0209585000132 gas there =  0.00687163267881 total SFR =  [ 0.00010934  0.01093441  0.01992044  0.02721847  0.03305797  0.03764088
  0.04114478  0.04372554  0.04551984  0.04664735  0.04721262  0.04730689
  0.04700961  0.04638979  0.04550726  0.04441377  0.04315389  0.04176597
  0.04028281] gas needed =  0.0278301324824 corona =  0.761693233124 sfe =  1.352522666 dt =  0.5
too few gas requested infall needed=  0.0224037709537 gas there =  0.0080169971599 total SFR =  [ 0.00010934  0.01093441  0.01992044  0.02721847  0.03305797  0.03764088
  0.04114478  0.04372554  0.04551984  0.04664735  0.04721262  0.04730689
  0.04700961  0.04638979  0.04550726  0.04441377  0.04315389  0.04176597
  0.04028281] gas needed =  0.0304207678895 corona =  0.773688035545 sfe =  1.352522666 dt =  0.5
too few gas requested infall needed=  0.0234196593993 gas there =  0.00890921752302 total SFR =  [ 0.00010934  0.01093441  0.01992044  0.02721847  0.03305797  0.03764088
  0

too few gas requested infall needed=  0.000910726107852 gas there =  0.000791303632068 total SFR =  [ 0.00014155  0.0141549   0.02525963  0.03380714  0.04021956  0.04485775
  0.04802959  0.04999721  0.0509833   0.0511765   0.05073624  0.04979676
  0.04847076  0.04685243  0.04502015  0.04303881  0.04096181  0.03883276
  0.03668698] gas needed =  0.00170202973081 corona =  1.00239007013 sfe =  29.9544104006 dt =  0.5
too few gas requested infall needed=  0.000900982009212 gas there =  0.000807497700103 total SFR =  [ 0.00014155  0.0141549   0.02525963  0.03380714  0.04021956  0.04485775
  0.04802959  0.04999721  0.0509833   0.0511765   0.05073624  0.04979676
  0.04847076  0.04685243  0.04502015  0.04303881  0.04096181  0.03883276
  0.03668698] gas needed =  0.0017084797003 corona =  1.0413196149 sfe =  29.9544104006 dt =  0.5
too few gas requested infall needed=  0.000882902191255 gas there =  0.000810879657021 total SFR =  [ 0.00014155  0.0141549   0.02525963  0.03380714  0.04021956  0.

too few gas requested infall needed=  0.0 gas there =  0.0120504470351 total SFR =  [  3.88947971e-05   8.89985939e-02   1.24911805e-01   1.31487688e-01
   1.23030891e-01   1.07923129e-01   9.08837250e-02   7.44086206e-02
   5.96768025e-02   4.71138302e-02   3.67363706e-02   2.83582402e-02
   2.17099180e-02   1.65048140e-02   1.24734233e-02   9.37862627e-03
   7.02034247e-03   5.23452866e-03   3.88947971e-03] gas needed =  0.00813365567307 corona =  1.25091804823 sfe =  5.7924544735 dt =  0.5
too few gas requested infall needed=  0.0 gas there =  0.0101989713198 total SFR =  [  3.88947971e-05   8.89985939e-02   1.24911805e-01   1.31487688e-01
   1.23030891e-01   1.07923129e-01   9.08837250e-02   7.44086206e-02
   5.96768025e-02   4.71138302e-02   3.67363706e-02   2.83582402e-02
   2.17099180e-02   1.65048140e-02   1.24734233e-02   9.37862627e-03
   7.02034247e-03   5.23452866e-03   3.88947971e-03] gas needed =  0.00634210778242 corona =  1.26064454048 sfe =  5.7924544735 dt =  0.5
too 

too few gas requested infall needed=  0.020858766398 gas there =  0.00283522954667 total SFR =  [  9.30771481e-05   9.30771481e-03   1.71639614e-02   2.37384989e-02
   2.91834381e-02   3.36349614e-02   3.72148819e-02   4.00320564e-02
   4.21836652e-02   4.37563713e-02   4.48273695e-02   4.54653361e-02
   4.57312878e-02   4.56793592e-02   4.53575044e-02   4.48081321e-02
   4.40686787e-02   4.31721257e-02   4.21474673e-02] gas needed =  0.0236939957361 corona =  0.731945480641 sfe =  1.78035252862 dt =  0.5
too few gas requested infall needed=  0.0214075798579 gas there =  0.00316978390707 total SFR =  [  9.30771481e-05   9.30771481e-03   1.71639614e-02   2.37384989e-02
   2.91834381e-02   3.36349614e-02   3.72148819e-02   4.00320564e-02
   4.21836652e-02   4.37563713e-02   4.48273695e-02   4.54653361e-02
   4.57312878e-02   4.56793592e-02   4.53575044e-02   4.48081321e-02
   4.40686787e-02   4.31721257e-02   4.21474673e-02] gas needed =  0.0245773635509 corona =  0.737546000182 sfe =  1

too few gas requested infall needed=  0.0328719878778 gas there =  0.00761204572068 total SFR =  [ 0.00020303  0.03370286  0.05519629  0.0677976   0.07402291  0.07576861
  0.07445325  0.07112849  0.06656541  0.06132171  0.05579366  0.05025632
  0.04489442  0.03982608  0.03512088  0.03081355  0.02691433  0.0234167
  0.0203031 ] gas needed =  0.0404840332698 corona =  1.17723390158 sfe =  1.64423868238 dt =  0.5
too few gas requested infall needed=  0.0300833596958 gas there =  0.00721153786516 total SFR =  [ 0.00020303  0.03370286  0.05519629  0.0677976   0.07402291  0.07576861
  0.07445325  0.07112849  0.06656541  0.06132171  0.05579366  0.05025632
  0.04489442  0.03982608  0.03512088  0.03081355  0.02691433  0.0234167
  0.0203031 ] gas needed =  0.0372948972601 corona =  1.20563386146 sfe =  1.64423868238 dt =  0.5
too few gas requested infall needed=  0.0271472294309 gas there =  0.00678559645544 total SFR =  [ 0.00020303  0.03370286  0.05519629  0.0677976   0.07402291  0.07576861
  

In [ ]:
from Chempy.cem_function import shorten_sfr
from Chempy.parameter import ModelParameters
a = ModelParameters()
shorten_sfr(a)

In [ ]:
%pylab inline

## To find SFR peak limits

In [ ]:
from scipy.stats import gamma
# Try for 8.4 as well...
sigma = np.linspace(1.32,1.35,10)
LHS = np.zeros(len(sigma))
RHS = np.zeros(len(sigma))
for i,s in enumerate(sigma):
    LHS[i] = gamma.pdf(9,2,0,s)
    RHS[i] = 0
    for j in range(int(2*9)):
        RHS[i]+=gamma.pdf(0.5*j+0.25,2,0,s)*2.96e-3
plt.plot(sigma,LHS,label='LHS')
plt.plot(sigma,RHS,label='RHS')
plt.legend()

In [ ]:
from Chempy.cem_function import shorten_sfr,extract_parameters_and_priors
from Chempy.parameter import ModelParameters
a = ModelParameters()
param = [-2.8,-2.5,-0.4,-0.1,0.083,0.7]
a = extract_parameters_and_priors(param,a)
shorten_sfr(a)
del a